## Препроцессинг данных

__Папка с данными на gdrive__

https://drive.google.com/drive/folders/1FeUwrVfxp09xAifiMngwtfrRZ8nhtj8T?usp=sharing



In [50]:
import pandas as pd
import numpy as np
import seaborn as sns
import folium
from matplotlib import pyplot as plt
from matplotlib import colors
from os import listdir
from tqdm import tqdm
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from snippets import *

%matplotlib inline

In [51]:
DATA_PATH = "../../data"

GPS_PATH = f"{DATA_PATH}/gps_data.csv"
ACCEL_PATH = f"{DATA_PATH}/accel_data.csv"

listdir(DATA_PATH)

['data_good_right_dates',
 'drivers_stats.csv',
 'gps_data.csv',
 'unlabeled',
 'gps_data_raw.csv',
 'good_data',
 'points_stats.csv',
 'accel_data.csv',
 'accel_data_raw.csv',
 'drivers_with_gps_and_sl_problems',
 'gps_stats.csv',
 'rides_of_drivers.csv',
 'accel_stats.csv']

## Датасет GPS

In [52]:
df_gps = pd.read_csv(GPS_PATH, parse_dates=[0, 3])
describe(df_gps)

dtypes        count                           mean  \
time           datetime64[ns]      5050292  2020-07-31 17:37:31.378774272   
lat                   float64  5.05029e+06                         55.743   
lon                   float64  5.05029e+06                        37.6021   
gps_time       datetime64[ns]      5050292  2020-07-31 17:37:28.866647296   
driver_hash             int64  5.05029e+06                    3.03558e+17   
fraud                   int64  5.05029e+06                      -0.767609   
gps_delta             float64  5.05029e+06                        6.85008   
gps_distance          float64  5.05029e+06                         19.588   
gps_speed             float64  5.05029e+06                        5.64977   
gps_accel             float64  5.05029e+06                     -0.0740194   
tm_delta              float64  5.05029e+06                        6.87986   
tm_distance           float64  5.05029e+06                        20.2285   
tm_speed              float64  5.05029e+06                        6.30422   
tm_accel              float64  5.05029e+06                      0.0702472   
diff_time             float64  5.05029e+06                       0.686299   
diff_distance         float64  5.05029e+06                         0.8069   
diff_speed            float64  5.05029e+06                       0.697568   
diff_accel            float64  5.05029e+06                       0.594992   

                               min                            25%  \
time           2015-03-01 03:00:02  2020-11-20 07:07:20.750000128   
lat                          42.98                        55.6674   
lon                        26.1013                        37.5009   
gps_time       2015-03-01 03:00:02  2020-11-20 07:07:20.750000128   
driver_hash           -9.21858e+18                   -4.06958e+18   
fraud                           -1                             -1   
gps_delta                        0                              2   
gps_distance                     0                              0   
gps_speed                        0                              0   
gps_accel                     -100                      -0.111111   
tm_delta                         0                              2   
tm_distance                      0                              0   
tm_speed                         0                              0   
tm_accel                      -100                      -0.111111   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_accel                       0                              0   

                               50%                            75%  \
time           2021-03-05 11:16:20  2021-06-03 21:19:25.750000128   
lat                        55.7496                        55.8242   
lon                        37.5848                        37.7032   
gps_time       2021-03-05 11:16:20  2021-06-03 21:19:25.750000128   
driver_hash            1.02237e+17                    4.79299e+18   
fraud                           -1                             -1   
gps_delta                        3                              3   
gps_distance                     5                             25   
gps_speed                        2                        9.66667   
gps_accel                        0                       0.111111   
tm_delta                         3                              3   
tm_distance                      5                             25   
tm_speed                         2                             10   
tm_accel                         0                       0.111111   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_

(5050292, 18)

## Датасет акселерометра

In [53]:
df_accel = pd.read_csv(ACCEL_PATH, parse_dates=[0])
describe(df_accel)

dtypes        count                           mean  \
time         datetime64[ns]      2172989  2020-11-22 12:54:59.282576896   
x                   float64  2.17299e+06                       0.368934   
y                   float64  2.17299e+06                         7.6569   
z                   float64  2.17299e+06                        3.83295   
lat                 float64  2.17299e+06                        55.7482   
lon                 float64  2.17299e+06                         37.601   
driver_hash           int64  2.17299e+06                   -1.12657e+17   
fraud                 int64  2.17299e+06                      -0.796897   
ac_delta            float64  2.17299e+06                        11.2106   
ac_distance         float64  2.17299e+06                         185.61   
ac_speed            float64  2.17299e+06                        78.3813   
ac_accel            float64  2.17299e+06                        28.7075   

                             min                  25%                  50%  \
time         2015-02-28 05:46:43  2020-12-18 06:53:34  2021-03-18 16:54:01   
x                       -71.1054            -0.371101             0.184359   
y                       -74.7916              7.63271              8.85376   
z                       -65.5062              2.01402              3.69992   
lat                      55.3163              55.6768              55.7512   
lon                      36.3143              37.5016              37.5863   
driver_hash         -9.21858e+18         -4.47912e+18         -4.14168e+17   
fraud                         -1                   -1                   -1   
ac_delta                       0                    0                    0   
ac_distance                    0                   11                   77   
ac_speed                       0                  100                  100   
ac_accel                    -100              28.7075              28.7075   

                             75%                  max         std  
time         2021-06-12 11:02:19  2021-08-29 00:03:16         NaN  
x                       0.785298              65.1529     2.36914  
y                        9.50019              55.2294      3.4034  
z                        5.35365              76.4756     2.73072  
lat                      55.8214              82.4343     0.16893  
lon                       37.686              108.856    0.376061  
driver_hash          4.43147e+18          9.20647e+18  5.3536e+18  
fraud                         -1                    1    0.509161  
ac_delta                       0                 3600      118.59  
ac_distance                  230                10000     399.524  
ac_speed                     100                  100     40.4896  
ac_accel                 28.7075                  100     37.3881

(2172989, 12)

In [54]:
# [None, -1, 0, 1]
FORCE_FRAUD = None

# Выбор случайного водителя
driver_gps, driver_hash, driver_fraud = sample_driver(df_gps, FORCE_FRAUD)
driver_accel = df_accel[df_accel["driver_hash"] == driver_hash]

center = (driver_gps["lat"].mean(), driver_gps["lon"].mean())
m = folium.Map(location=center, zoom_start=10, legend=True)

# Маршрут по данным акселерометра
driver_accel = driver_accel.sort_values(by="time").reset_index(drop=True)
map_driver_points(m, driver_accel, driver_hash, label="accel", color="blue")

# Маршрут по данным  GPS
driver_gps = driver_gps.sort_values(by="gps_time").reset_index(drop=True)
map_driver_points(m, driver_gps, driver_hash, label="gps")

folium.map.LayerControl('topleft', collapsed= False).add_to(m)
m

In [55]:
MERGE_TOLERANCE = "600s"

df_merged = pd.merge_asof(driver_gps, driver_accel,
              left_on="gps_time",
              right_on="time",
              direction="nearest",
              tolerance=pd.Timedelta(MERGE_TOLERANCE),
              suffixes=("", "_r"),
              allow_exact_matches=False)

df_matched = df_merged.dropna(thresh=len(df_gps.columns) + len(df_accel.columns)) \
    .copy() \
    .drop(columns=["driver_hash_r", "fraud_r"]) \
    .rename(columns={"time_r": "accel_time", "lat_r": "accel_lat", "lon_r": "accel_lon",
                     "time_diff_r": "accel_time_diff", "distance_r": "accel_distance",
                     "speed_r": "accel_speed", "route_by_time_r": "route_by_accel",
                     "x": "accel_x", "y": "accel_y", "z": "accel_z"
                    })

display(f"{driver_hash} Matched: {df_matched.shape[0]} of {df_merged.shape[0]}")
if df_matched.shape[0] > 0:
    describe(df_matched)

'-4294745953159109974 Matched: 38204 of 40827'

dtypes  count                           mean  \
time           datetime64[ns]  38204  2015-03-30 04:21:13.728510208   
lat                   float64  38204                        55.7178   
lon                   float64  38204                        37.7646   
gps_time       datetime64[ns]  38204  2015-03-30 04:21:04.057847296   
driver_hash             int64  38204                   -4.29475e+18   
fraud                   int64  38204                              0   
gps_delta             float64  38204                        2.90127   
gps_distance          float64  38204                        17.1482   
gps_speed             float64  38204                        6.53073   
gps_accel             float64  38204                     -0.0468527   
tm_delta              float64  38204                        2.90119   
tm_distance           float64  38204                        18.9765   
tm_speed              float64  38204                         9.3076   
tm_accel              float64  38204                      0.0631133   
diff_time             float64  38204                       0.258271   
diff_distance         float64  38204                        1.82892   
diff_speed            float64  38204                        2.79602   
diff_accel            float64  38204                       0.907373   
accel_time     datetime64[ns]  38204  2015-03-30 04:20:56.333839616   
accel_x               float64  38204                      0.0860184   
accel_y               float64  38204                        8.64192   
accel_z               float64  38204                        3.76655   
accel_lat             float64  38204                        55.7181   
accel_lon             float64  38204                        37.7643   
ac_delta              float64  38204                        100.617   
ac_distance           float64  38204                        448.913   
ac_speed              float64  38204                        54.9029   
ac_accel              float64  38204                        24.0962   

                               min                            25%  \
time           2015-03-29 07:46:16  2015-03-29 16:00:39.249999872   
lat                        55.6217                        55.6748   
lon                        37.6009                        37.7173   
gps_time       2015-03-29 07:46:16  2015-03-29 16:00:39.249999872   
driver_hash           -4.29475e+18                   -4.29475e+18   
fraud                            0                              0   
gps_delta                        0                              2   
gps_distance                     0                              0   
gps_speed                        0                              0   
gps_accel                     -100                          -0.25   
tm_delta                         0                              2   
tm_distance                      0                              0   
tm_speed                         0                              0   
tm_accel                      -100                          -0.25   
diff_time                        0                              0   
diff_distance                    0                              0   
diff_speed                       0                              0   
diff_accel                       0                              0   
accel_time     2015-03-29 07:47:07            2015-03-29 16:00:29   
accel_x                   -15.2688                      -0.180197   
accel_y                   -11.5086                        8.47975   
accel_z                   -10.4164                        3.23386   
accel_lat                  55.6222                        55.6762   
accel_lon                  37.6009                        37.7189   
ac_delta                         0                              0   
ac_distance                      0                             23   
ac_speed                         0                        3.10833   
ac_accel                      -

(38204, 28)

In [56]:
gps_time_diff = df_matched["gps_time"].diff()
gps_time_diff.fillna(gps_time_diff.mean(), inplace=True)
display(gps_time_diff.round("5min").value_counts())

accel_time_diff = df_matched["accel_time"].diff()
accel_time_diff.fillna(accel_time_diff.diff().mean(), inplace=True)
display(accel_time_diff.round("5min").value_counts())

0 days 00:00:00    38183
0 days 00:05:00        7
0 days 00:10:00        6
0 days 00:20:00        2
0 days 00:25:00        2
0 days 00:40:00        1
0 days 08:25:00        1
0 days 01:25:00        1
0 days 00:15:00        1
Name: gps_time, dtype: int64

0 days 00:00:00      38140
0 days 00:05:00         33
0 days 00:10:00          8
0 days 00:15:00          7
0 days 00:20:00          3
-1 days +23:55:00        3
0 days 00:30:00          2
0 days 00:35:00          2
0 days 00:55:00          1
0 days 08:40:00          1
0 days 00:40:00          1
0 days 00:25:00          1
0 days 00:45:00          1
0 days 01:40:00          1
Name: accel_time, dtype: int64

In [57]:
df_matched["track"] = gps_time_diff.round("10min").cumsum().dt.seconds
number_of_tracks = len(df_matched["track"].unique())
display(f"Number of tracks: {number_of_tracks}")

df_matched = df_matched[["driver_hash", "fraud", "track"] + cols_gps[2:] + cols_accel[2:]].copy()
describe(df_matched)

'Number of tracks: 18'

dtypes  count                           mean  \
driver_hash           int64  38204                   -4.29475e+18   
fraud                 int64  38204                              0   
track                 int64  38204                        24499.3   
time         datetime64[ns]  38204  2015-03-30 04:21:13.728510208   
lat                 float64  38204                        55.7178   
lon                 float64  38204                        37.7646   
gps_time     datetime64[ns]  38204  2015-03-30 04:21:04.057847296   
accel_time   datetime64[ns]  38204  2015-03-30 04:20:56.333839616   
accel_lat           float64  38204                        55.7181   
accel_lon           float64  38204                        37.7643   
accel_x             float64  38204                      0.0860184   
accel_y             float64  38204                        8.64192   
accel_z             float64  38204                        3.76655   

                             min                            25%  \
driver_hash         -4.29475e+18                   -4.29475e+18   
fraud                          0                              0   
track                          0                           4800   
time         2015-03-29 07:46:16  2015-03-29 16:00:39.249999872   
lat                      55.6217                        55.6748   
lon                      37.6009                        37.7173   
gps_time     2015-03-29 07:46:16  2015-03-29 16:00:39.249999872   
accel_time   2015-03-29 07:47:07            2015-03-29 16:00:29   
accel_lat                55.6222                        55.6762   
accel_lon                37.6009                        37.7189   
accel_x                 -15.2688                      -0.180197   
accel_y                 -11.5086                        8.47975   
accel_z                 -10.4164                        3.23386   

                                    50%                            75%  \
driver_hash                -4.29475e+18                   -4.29475e+18   
fraud                                 0                              0   
track                             37200                          47400   
time         2015-03-30 07:53:31.500000  2015-03-30 17:34:01.750000128   
lat                             55.7114                        55.7563   
lon                             37.7567                        37.8185   
gps_time     2015-03-30 07:53:31.500000  2015-03-30 17:34:01.750000128   
accel_time          2015-03-30 07:52:58            2015-03-30 17:33:54   
accel_lat                       55.7122                        55.7565   
accel_lon                       37.7545                        37.8174   
accel_x                        0.259254                       0.647699   
accel_y                           8.838                        9.15485   
accel_z                         3.79053                        4.27694   

                             max        std  
driver_hash         -4.29475e+18          0  
fraud                          0          0  
track                      49200    20680.7  
time         2015-03-31 01:29:45        NaN  
lat                      55.8274  0.0493196  
lon                      37.9408  0.0727329  
gps_time     2015-03-31 01:29:44        NaN  
accel_time   2015-03-31 01:20:38        NaN  
accel_lat                55.8271  0.0494421  
accel_lon                37.9406  0.0725094  
accel_x                  13.3732    1.49374  
accel_y                  15.2703    1.56832  
accel_z                  14.9343    1.50465

(38204, 13)

In [58]:
df_matched

driver_hash  fraud  track                time        lat  \
9     -4294745953159109974      0      0 2015-03-29 07:46:16  55.647351   
10    -4294745953159109974      0      0 2015-03-29 07:46:19  55.647500   
11    -4294745953159109974      0      0 2015-03-29 07:46:19  55.647500   
12    -4294745953159109974      0      0 2015-03-29 07:46:20  55.647158   
13    -4294745953159109974      0      0 2015-03-29 07:46:23  55.647155   
...                    ...    ...    ...                 ...        ...   
40633 -4294745953159109974      0  49200 2015-03-31 01:29:20  55.694439   
40634 -4294745953159109974      0  49200 2015-03-31 01:29:23  55.694192   
40635 -4294745953159109974      0  49200 2015-03-31 01:29:26  55.693961   
40636 -4294745953159109974      0  49200 2015-03-31 01:29:42  55.692796   
40637 -4294745953159109974      0  49200 2015-03-31 01:29:45  55.692571   

             lon            gps_time          accel_time  accel_lat  \
9      37.721282 2015-03-29 07:46:16 2015-03-29 07:47:07  55.647154   
10     37.720908 2015-03-29 07:46:18 2015-03-29 07:47:07  55.647154   
11     37.720908 2015-03-29 07:46:19 2015-03-29 07:47:07  55.647154   
12     37.721549 2015-03-29 07:46:20 2015-03-29 07:47:07  55.647154   
13     37.721691 2015-03-29 07:46:23 2015-03-29 07:47:07  55.647154   
...          ...                 ...                 ...        ...   
40633  37.712870 2015-03-31 01:29:19 2015-03-31 01:20:38  55.691712   
40634  37.713091 2015-03-31 01:29:22 2015-03-31 01:20:38  55.691712   
40635  37.713417 2015-03-31 01:29:25 2015-03-31 01:20:38  55.691712   
40636  37.715105 2015-03-31 01:29:42 2015-03-31 01:20:38  55.691712   
40637  37.715069 2015-03-31 01:29:44 2015-03-31 01:20:38  55.691712   

       accel_lon   accel_x    accel_y   accel_z  
9      37.721708  0.980665   7.768428  5.956458  
10     37.721708  0.980665   7.768428  5.956458  
11     37.721708  0.980665   7.768428  5.956458  
12     37.721708  0.980665   7.768428  5.956458  
13     37.721708  0.980665   7.768428  5.956458  
...          ...       ...        ...       ...  
40633  37.663064 -6.692665 -11.508574 -1.331827  
40634  37.663064 -6.692665 -11.508574 -1.331827  
40635  37.663064 -6.692665 -11.508574 -1.331827  
40636  37.663064 -6.692665 -11.508574 -1.331827  
40637  37.663064 -6.692665 -11.508574 -1.331827  

[38204 rows x 13 columns]

In [59]:
center = (df_matched["lat"].mean(), df_matched["lon"].mean())
m = folium.Map(location=center, zoom_start=10, legend=True)

color = driver_accel.head(1)["fraud"].replace({1:"red", 0:"green", -1:"yellow"}).values[0]

for track in df_matched["track"].unique():
    fg = folium.FeatureGroup(name=f"track{track}")
    gps_track = df_matched[df_matched["track"] == track]
    folium.PolyLine(gps_track[["lat", "lon"]], color="blue", weight=8, label="accel", opacity=0.8).add_to(fg)
    accel_track = df_matched[df_matched["track"] == track]
    folium.PolyLine(accel_track[["accel_lat", "accel_lon"]], color=color, weight=6, label="tracks", opacity=0.8).add_to(fg)
    fg.add_to(m)

folium.map.LayerControl('topleft', collapsed=False).add_to(m)
m

### Вывод - такая разбивка на поездки выглядит вполне правдоподобной